### Config TemplateFlow

In [1]:
# Test if singularity correctly setting Home binding
!export SINGULARITYENV_TEMPLATEFLOW_HOME=/imaging/jj02/templateflow

In [ ]:
!git config --global user.name "JoffJones"
!git config --global user.email "Jonathan.Jones@mrc-cbu.cam.ac.uk"

In [ ]:
from templateflow.api import templates, get
templates()

## Download relevant templates

In [ ]:
# Needed for Carpet Plots

import templateflow.api
templateflow.api.TF_S3_ROOT = 'http://templateflow.s3.amazonaws.com'
get('MNI152NLin2009cAsym')

In [ ]:
# Standard Template

import templateflow.api
templateflow.api.TF_S3_ROOT = 'http://templateflow.s3.amazonaws.com'
get('MNI152NLin6Asym')

In [ ]:
import templateflow.api
templateflow.api.TF_S3_ROOT = 'http://templateflow.s3.amazonaws.com'
get('MNIPediatricAsym')

In [ ]:
# Needed for freesurfer recon-all (surface reconstruction)

import templateflow.api
templateflow.api.TF_S3_ROOT = 'http://templateflow.s3.amazonaws.com'
get('fsaverage')

In [ ]:
import templateflow.api
templateflow.api.TF_S3_ROOT = 'http://templateflow.s3.amazonaws.com'
get('fsnative')

In [ ]:
# Standard skull strip template

import templateflow.api
templateflow.api.TF_S3_ROOT = 'http://templateflow.s3.amazonaws.com'
get('OASIS30ANTs')

## Run fmriprep

In [ ]:
import os, subprocess

# setup template flow environment
my_env = os.environ.copy()
my_env["SINGULARITYENV_TEMPLATEFLOW_HOME"] = "/templateflow"

# directories
bids_dir = '/path/to/bids'
slurm_output_dir = '/path/to/cluster/log/files'
os.mkdir(slurm_output_dir)

# set range of BIDS_ID numbers to be processed
for n in range(1, 100):
    p = subprocess.run(" ".join(["sbatch", "--mincpus=6", "--time=48:00:00", #sbatch cmd
                         "--job-name=fmriprep", 
                         "--output", slurm_output_dir + "/sub-%03d.out" %(n),
                         "singularity", "exec", "-C", #singularity call
                         "-B", "/imaging/jj02/CALM:/CALM", # freesurfer license location
                         "-B", bids_dir + ":/bids", # bids directory
                         "-B", "/home/jj02/.cache/templateflow:/templateflow", # these might need to be set to your home
                         "-B", "/home/jj02/.cache/fmriprep:/home/fmriprep", # these might need to be set to your home
                         "-B", "/tmp:/tmp",
                         "/imaging/local/software/singularity_images/fmriprep/fmriprep-1.5.0.simg", # singularity image
                         "fmriprep", # run fmriprep
                         "/bids", # bids directory
                         "/bids/derivatives/fmriprep-1.5.0", # fmriprep directory
                         "participant", "--participant_label", '%03d' %(n), # participant info
                         "-v", "-w", "/bids/derivatives/fmriprepwork-1.5.0", # wording directory
                         "--skull-strip-template", "MNIPediatricAsym:cohort-1", # child skull-strip template
                         "--output-spaces", "MNIPediatricAsym:cohort-1:res-2", "T1w", # child template
                         "MNI152NLin6Asym:res-2", "MNI152NLin2009cAsym", # For ICA-AROMA & carpet plot
                         "fsaverage", # For freesurfer BBR and surface-based BOLD
                         "--use-aroma", # ICA-AROMA denoising output
                         "--fs-license-file", "/CALM/license.txt", # freesurfer license
                         "--write-graph",
                         "--fd-spike-threshold", "0.5", "--dvars-spike-threshold", "0.5",
                         "--notrack", "--resource-monitor",
                         "--skip-bids-validation"]), # skip this for cluster jobs as it tries to go online
                        shell=True, stdout=subprocess.PIPE, stderr=subprocess.PIPE, env=my_env)
    print(p.args)
    print(p.stdout.decode())
    print(p.stderr.decode())

## MRIQC

In [ ]:
# Run participant-level mriqc
import subprocess

# directories
bids_dir = '/path/to/bids'
slurm_output_dir = '/path/to/cluster/log/files'
os.mkdir(slurm_output_dir)

# set range of BIDS_ID numbers to be processed
for i in range(1, 100):
    p = subprocess.Popen(("sbatch", "--mincpus=1", "--job-name=mriqc", #sbatch cmd
                          "--output", slurm_output_dir + "/sub-%03d.out" %(i), 
                          "singularity", "run", "-C", 
                          "-B", bids_dir + ":/bids",
                          "/imaging/local/software/singularity_images/mriqc/mriqc-0.14.2.simg",
                          "/bids", "/bids/derivatives/mriqc", #dirs
                          "participant", "--participant-label", "%03d" %(i),
                          "--fd_thres", "0.5", 
                          "--verbose-reports", "--no-sub", #mriqc options
                          "-v", "-w", "/bids/derivatives/mriqcwork"),
                        shell=False, stdout=subprocess.PIPE, stderr=subprocess.PIPE)

In [ ]:
# Run group-level mriqc
import subprocess

p = subprocess.Popen(("sbatch", "--mem-per-cpu=64gb", "--job-name=mriqc", #sbatch cmd
                      "--output", "/imaging/jj02/CALM/slurm/mriqc/group.out", 
                      "singularity", "run", "-C", 
                      "-B", bids_dir + ":/bids",
                      "/imaging/local/software/singularity_images/mriqc/mriqc-0.14.2.simg",
                      "/bids", "/bids/derivatives/mriqc", #dirs
                      "group", 
                      "--fd_thres", "0.5",
                      "--verbose-reports", "--no-sub", #mriqc options
                      "-v", "-w", "/bids/derivatives/mriqcwork"),
                    shell=False, stdout=subprocess.PIPE, stderr=subprocess.PIPE)

In [ ]:
# Run MRIQC classifier
!singularity exec -B /path/to/BIDS:/bids /imaging/local/software/singularity_images/mriqc/mriqc-0.14.2.simg \
        mriqc_clf --verbose --load-classifier -X /bids/derivatives/mriqc/group_T1w.tsv